* [Issue 2](https://github.com/salgo60/Dogpark_Sweden/issues/2)
* denna notebook [Dogpark_Sweden.ipynb](https://github.com/salgo60/Dogpark_Sweden/blob/main/notebook/Dogpark_Sweden.ipynb)

In [2]:
import requests, json, time
from bs4 import BeautifulSoup

BASE_URL = "https://www.hundlistan.se/"
params = {
    "mylisting-ajax": "1",
    "action": "get_listings",
    "security": "5e528da4d5",  # säkerhets-token (kan behöva uppdateras om Hundlistan ändrar den)
    "form_data[preserve_page]": "true",
    "form_data[sort]": "latest",
    "form_data[region]": "",
    "form_data[search_location]": "",
    "form_data[lat]": "false",
    "form_data[lng]": "false",
    "listing_type": "hundpark",
    "listing_wrap": "col-md-12 grid-item"
}

features = []

for page in range(1, 40):  # 1 till 39
    params["form_data[page]"] = str(page)
    print(f"Hämtar sida {page}/39 ...", end="\r")

    r = requests.get(BASE_URL, params=params)
    if r.status_code != 200:
        print(f"\n⚠️ Sida {page} misslyckades ({r.status_code})")
        continue

    data = r.json()
    html = data.get("html", "")
    soup = BeautifulSoup(html, "html.parser")

    for item in soup.select(".lf-item-container"):
        try:
            data_id = item.get("data-id")
            title = item.select_one(".listing-preview-title").get_text(strip=True)
            href = item.select_one("a")["href"]
            lan = item.select_one(".lf-contact li").get_text(strip=True)
            loc = json.loads(item.get("data-locations"))[0]

            address = loc.get("address")
            lat = float(loc.get("lat"))
            lng = float(loc.get("lng"))

            popup_html = f"""
            <b>{title}</b><br>
            {address}<br>
            {lan}<br>
            <a href="{href}" target="_blank">Visa på Hundlistan</a>
            """.strip()

            features.append({
                "type": "Feature",
                "geometry": {"type": "Point", "coordinates": [lng, lat]},
                "properties": {
                    "id": data_id,
                    "namn": title,
                    "adress": address,
                    "lan": lan,
                    "url": href,
                    "popup": popup_html
                }
            })
        except Exception as e:
            print(f"\n⚠️ Fel vid parsing: {e}")

    time.sleep(0.5)  # vänlig delay mot servern

geojson = {
    "type": "FeatureCollection",
    "features": features
}

with open("hundparker_umap.geojson", "w", encoding="utf-8") as f:
    json.dump(geojson, f, ensure_ascii=False, indent=2)

print(f"\n✅ Klart! {len(features)} hundparker sparade i hundparker_umap.geojson")


Hämtar sida 39/39 ...
✅ Klart! 760 hundparker sparade i hundparker_umap.geojson


### Skapa karta


In [3]:
import folium
import json

# Läs in GeoJSON-filen
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

# Skapa grundkartan (centrerad på Sverige)
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# Gå igenom varje hundpark och skapa en marker
for feature in data["features"]:
    props = feature["properties"]
    coords = feature["geometry"]["coordinates"]
    lon, lat = coords[0], coords[1]

    # Popup med tydlig formatering
    popup_html = f"""
    <div style="font-family: Arial; font-size: 13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {props['namn']}</b><br>
      <span style="color:#555;">📍 {props.get('adress', 'Okänd adress')}</span><br>
      <span style="color:#555;">🏙️ {props.get('lan', 'Okänt län')}</span><br>
      <a href="{props['url']}" target="_blank" style="color:#0077cc; text-decoration:none;">
        🔗 Visa på Hundlistan
      </a>
    </div>
    """

    folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=props["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(m)

# Lägg till lagerkontroll
folium.LayerControl().add_to(m)

# Spara kartan
m.save("hundparker_folium_snygg.html")
print("✅ Snygg Folium-karta sparad som hundparker_folium_snygg.html")


✅ Snygg Folium-karta sparad som hundparker_folium_snygg.html


In [4]:
m

In [5]:
import folium
import json

# Läs in GeoJSON
with open("hundparker_umap.geojson", "r", encoding="utf-8") as f:
    data = json.load(f)

# Skapa kartan
m = folium.Map(location=[62.0, 16.0], zoom_start=5, tiles="CartoDB positron")

# Lägg till infobox med logga och GitHub-länk
info_html = """
<div style="
    position: fixed; 
    top: 10px; left: 10px; 
    z-index: 9999; 
    background-color: rgba(255,255,255,0.9); 
    padding: 10px; 
    border-radius: 12px; 
    box-shadow: 0 0 10px rgba(0,0,0,0.2);
    font-family: Arial; font-size: 13px;">
  <div style="text-align:center;">
    <img src="https://raw.githubusercontent.com/salgo60/Dogpark_Sweden/main/dogparksweden.png" 
         alt="Dogpark Sweden" width="180"><br>
    <a href="https://github.com/salgo60/Dogpark_Sweden" target="_blank" 
       style="color:#0077cc; text-decoration:none; font-weight:bold;">
       🐾 Dogpark Sweden på GitHub
    </a>
  </div>
</div>
"""
m.get_root().html.add_child(folium.Element(info_html))

# Lägg till markörer
for f in data["features"]:
    p = f["properties"]
    lon, lat = f["geometry"]["coordinates"]
    popup_html = f"""
    <div style="font-family:Arial; font-size:13px;">
      <b style="font-size:14px; color:#2b7a78;">🐾 {p['namn']}</b><br>
      📍 {p.get('adress','Okänd adress')}<br>
      🏙️ {p.get('lan','Okänt län')}<br>
      <a href="{p['url']}" target="_blank" style="color:#0077cc;">🔗 Visa på Hundlistan</a>
    </div>
    """
    folium.Marker(
        [lat, lon],
        popup=folium.Popup(popup_html, max_width=300),
        tooltip=p["namn"],
        icon=folium.Icon(color="green", icon="paw", prefix="fa")
    ).add_to(m)

m.save("hundparker_folium_dogparksweden_2.html")
print("✅ Karta skapad: hundparker_folium_dogparksweden_2.html")


✅ Karta skapad: hundparker_folium_dogparksweden_2.html


In [6]:
m
